#### Dependecies

scipy = 0.17.0
gensim = 1.0.1
pandas = 0.19.2
numpy = 1.11.2

#### I used DATA_HADM.csv from feature_extraction_nonseq.ipynb 

In [4]:
import pandas as pd
import pickle

df_hadm_top10 = pd.read_csv("./data/DATA_HADM_CLEANED_top10_icd9code.csv", escapechar='\\')
ICD9CODES = pickle.load(open("./data/ICD9CODES.p", "rb"))

df_hadm_top10.head(50)

id                                               text  4019  4280  \
0   100001  admission date discharge date date birth sex f...     0     0   
1   100003  admission date discharge date date birth sex s...     1     0   
2   100006  admission date discharge date date birth sex f...     0     0   
3   100007  admission date discharge date date birth sex f...     1     0   
4   100009  admission date discharge date date birth sex s...     1     0   
5   100010  admission date discharge date date birth sex f...     0     0   
6   100011  admission date discharge date date birth sex s...     0     0   
7   100012  admission date discharge date date birth sex s...     1     0   
8   100016  admission date discharge date date birth sex s...     0     0   
9   100018  admission date discharge date date birth sex s...     0     1   
10  100019  admission date discharge date date birth sex s...     0     0   
11  100020  admission date discharge date date birth sex s...     1     1   
12  100021  admission date discharge date date birth sex s...     1     0   
13  100024  admission date discharge date date birth sex s...     1     0   
14  100025  admission date discharge date date birth sex s...     0     0   
15  100028  admission date discharge date date birth sex f...     0     0   
16  100029  admission date discharge date date birth sex f...     0     0   
17  100030  admission date discharge date date birth sex s...     0     0   
18  100031  admission date discharge date service cardioth...     1     0   
19  100034  admission date discharge date date birth sex s...     1     0   
20  100035  admission date discharge date date birth sex s...     0     1   
21  100036  admission date discharge date date birth sex f...     0     1   
22  100037  admission date discharge date date birth sex s...     1     0   
23  100038  admission date discharge date date birth sex f...     1     0   
24  100039  admission date discharge date date birth sex f...     0     1   
25  100040  admission date discharge date date birth sex s...     1     0   
26  100041  admission date discharge date date birth sex s...     1     0   
27  100044  admission date discharge date date birth sex s...     0     0   
28  100045  admission date discharge date date birth sex f...     0     0   
29  100046  admission date discharge date date birth sex f...     0     0   
30  100050  admission date discharge date date birth sex s...     0     1   
31  100053  admission date discharge date date birth sex s...     0     0   
32  100058  admission date discharge date date birth sex f...     0     0   
33  100059  admission date discharge date date birth sex s...     1     0   
34  100060  admission date discharge date date birth sex f...     0     0   
35  100061  admission date discharge date date birth sex f...     0     1   
36  100062  admission date discharge date date birth sex f...     0     0   
37  100063  admission date discharge date date birth sex s...     1     0   
38  100065  admission date discharge date date birth sex s...     1     0   
39  100066  admission date discharge date date birth sex f...     1     0   
40  100068  admission date discharge date date birth sex f...     0     1   
41  100071  admission date discharge date date birth sex f...     0     0   
42  100074  admission date discharge date date birth sex f...     0     0   
43  100075  admission date discharge date date birth sex s...     0     0   
44  100077  admission date discharge date date birth sex f...     0     0   
45  100078  admission date discharge date date birth sex f...     1     1   
46  100081  admission date discharge date date birth sex f...     0     0   
47  100085  admission date discharge date date birth sex f...     1     0   
48  100087  admission date discharge date date birth sex s...     1     1   
49  100088  admission date discharge date date birth sex f...     0     0   

    42731  41401  5849  25000  2724  51881  5990  53081  
0       0      0     1

In [3]:
df_hadm_top10.iloc[33]['text']

'admission date discharge date date birth sex service csu history present illness year old white male abnormal stress test underwent cardiac cath revealed percent rca lesion angina abnormal stress test cathed showed percent rca lesion percent left main stenosis left circumflex stenosis symptoms surgery deferred month angina abnormal treadmill ef percent angio revealed percent ostia left main percent diagonal lesion percent om percent rca lesion normal lv transferred treatment past medical history past medical history significant history non insulin dependent diabetes hypercholesterolemia hypertension prostate ca status post removal basal cell carcinoma back two weeks prior admission also status post cataract surgery medications medications admission nitroglycerin drip metformin lipitor aspirin multivitamin metamucil atenolol allergies known allergies family history family history significant coronary artery disease social history smoke cigarettes drinks alcohol occasionally review syst

In [5]:
import numpy as np
import re
from sklearn.feature_extraction.text import TfidfVectorizer


def preprocessor_v1(text):
    text = re.sub('\[\*\*[^\]]*\*\*\]', '', text)
    text = re.sub('<[^>]*>', '', text)
    text = re.sub('[\W]+', ' ', text.lower()) 
    return text

def create_TFIDF_v1(df_train, df_apply, inputCol="text", outputCol="features",
                    minDocFreq=3, maxDocFreq=1.0, numFeatures=20):
    df_train['z_cleaned'] = df_train[inputCol].apply(preprocessor_v1)
    df_apply['z_cleaned'] = df_apply[inputCol].apply(preprocessor_v1)

    # Now we create the sparse matrix of tfidf values
    tfidf = TfidfVectorizer(input='content',ngram_range=(1, 1),
                            stop_words=STOPWORDS_v1, 
                            min_df=minDocFreq,
                            max_df=maxDocFreq,
                            max_features=numFeatures)
    # I select to remove stopwords and minimun doc frequency =10 to delete very unusual words
    # that only show up in less than 10 notes (out of 59k notes available) 

    tfidf.fit([c for c in df_train['z_cleaned']])
    dtm = tfidf.transform([c for c in df_apply['z_cleaned']]).tocsr()
    dtm.sort_indices()
    df_apply[outputCol] = list(dtm)
   
    del df_train['z_cleaned']
    del df_apply['z_cleaned']
    del df_apply[inputCol]
    
    return df_apply

In [6]:
import random

def separate(seed, N):    
    idx=list(range(N))
    random.seed(seed)
    random.shuffle(idx)
    idx_train= idx[0:int(N*0.50)]
    idx_val= idx[int(N*0.50):int(N*0.75)]
    idx_test= idx[int(N*0.75):N]

    return idx_train, idx_val, idx_test


idx_train, idx_val, idx_test = separate(1234, df_hadm_top10.shape[0])
idx_join_train=idx_train + idx_val
len(idx_join_train)

39544

In [7]:
df_hadm_top10_d2v=df_hadm_top10.iloc[idx_join_train].copy()
df_hadm_top10_d2v.head(5)

id                                               text  4019  4280  \
48602  192120  admission date discharge date date birth sex f...     0     0   
35229  167005  admission date discharge date date birth sex s...     0     1   
11870  122438  admission date discharge date date birth sex f...     1     0   
41322  178371  admission date discharge date date birth sex s...     1     0   
3767   107054  admission date discharge date date birth sex s...     1     0   

       42731  41401  5849  25000  2724  51881  5990  53081  
48602      0      0     0      0     0      0     1      0  
35229      1      1     1      0     0      0     1      0  
11870      0      0     0      0     0      0     0      0  
41322      0      0     0      1     0      0     0      0  
3767       0      0     0      0     0      0     0      1

### Apply doc2vec

In [8]:
# Cleanning the data
# Light preprocesing done on purpose (so word2vec understand sentence structure)
import re
def preprocessor(text):
    text = re.sub('<[^>]*>', '', text)
    text = re.sub('[\W]+', ' ', text.lower())
    text = text.split()
    return text

token_review = list(df_hadm_top10_d2v['text'].apply(preprocessor))
len(token_review)

39544

In [9]:
token_review[0]

['admission',
 'date',
 'discharge',
 'date',
 'date',
 'birth',
 'sex',
 'f',
 'service',
 'medicine',
 'allergies',
 'patient',
 'recorded',
 'known',
 'allergies',
 'drugs',
 'attending',
 'chief',
 'complaint',
 'acute',
 'hepatitis',
 'likely',
 'acetaminophen',
 'toxicity',
 'reason',
 'transfer',
 'treatment',
 'acute',
 'kidney',
 'injury',
 'hepatitis',
 'major',
 'surgical',
 'invasive',
 'procedure',
 'dialysis',
 'catheter',
 'placement',
 'history',
 'present',
 'illness',
 'patient',
 'year',
 'old',
 'woman',
 'history',
 'anxiety',
 'depression',
 'prior',
 'suicide',
 'attempts',
 'presented',
 'ed',
 'suicide',
 'attempt',
 'per',
 'chart',
 'notes',
 'patient',
 'found',
 'pregnant',
 'weeks',
 'ago',
 'told',
 'boyfriend',
 'offered',
 'money',
 'terminate',
 'pregnancy',
 'miscarried',
 'underwent',
 'c',
 'felt',
 'quite',
 'hopeless',
 'upset',
 'per',
 'records',
 'ingested',
 'tabs',
 'mg',
 'tylenol',
 'gm',
 'tabs',
 'mg',
 'xanax',
 'mg',
 'midnight',
 'take

In [12]:
import gensim
from gensim.models.doc2vec import TaggedDocument
LabeledSentence = gensim.models.doc2vec.LabeledSentence
    
def labelizeReviews(reviews, label_type):
    labelized = []
    for i,v in enumerate(reviews):
        label = '%s_%s'%(label_type,i)
        labelized.append(TaggedDocument(v, [label]))
    return labelized


In [13]:
sentence=labelizeReviews(token_review, "note")
len(sentence)

39544

In [14]:
sentence

[TaggedDocument(words=['admission', 'date', 'discharge', 'date', 'date', 'birth', 'sex', 'f', 'service', 'medicine', 'allergies', 'patient', 'recorded', 'known', 'allergies', 'drugs', 'attending', 'chief', 'complaint', 'acute', 'hepatitis', 'likely', 'acetaminophen', 'toxicity', 'reason', 'transfer', 'treatment', 'acute', 'kidney', 'injury', 'hepatitis', 'major', 'surgical', 'invasive', 'procedure', 'dialysis', 'catheter', 'placement', 'history', 'present', 'illness', 'patient', 'year', 'old', 'woman', 'history', 'anxiety', 'depression', 'prior', 'suicide', 'attempts', 'presented', 'ed', 'suicide', 'attempt', 'per', 'chart', 'notes', 'patient', 'found', 'pregnant', 'weeks', 'ago', 'told', 'boyfriend', 'offered', 'money', 'terminate', 'pregnancy', 'miscarried', 'underwent', 'c', 'felt', 'quite', 'hopeless', 'upset', 'per', 'records', 'ingested', 'tabs', 'mg', 'tylenol', 'gm', 'tabs', 'mg', 'xanax', 'mg', 'midnight', 'take', 'etoh', 'time', 'ingestion', 'last', 'drink', 'per', 'records',

In [15]:
from gensim.models import Doc2Vec
import gensim.models.doc2vec
from gensim import utils
from time import time

# assumptions: window is 5 words left and right, eliminate words than dont occur in
# more than 10 docs, use 4 workers for a quadcore machine. Size is the size of vector
# negative=5 implies negative sampling and makes doc2vec faster to train
#model = Doc2Vec(sentence, size=100, window=5, workers=4, min_count=5)


import random

vector_size = 600 #change to 100 and 300 to generate vector with those dimensions

#instantiate our model
model_dm = Doc2Vec(min_count=10, window=5, size=size, sample=1e-3, negative=5, workers=4)

#build vocab over all reviews
model_dm.build_vocab(sentence)

#We pass through the data set multiple times, shuffling the training reviews each time to improve accuracy.
Idx=list(range(len(sentence)))

t0 = time()
for epoch in range(5):
     random.shuffle(Idx)
     perm_sentences = [sentence[i] for i in Idx]
     model_dm.train(perm_sentences,total_examples=model_dm.corpus_count,epochs = model_dm.epochs)
     print(epoch)
    
elapsed=time() - t0
print("Time taken for Doc2vec training: ", elapsed, "seconds.")

C:\ProgramData\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:319: UserWarning: The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.
  warnings.warn("The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.")


ValueError: You must specify either total_examples or total_words, for proper job parameters updationand progress calculations. The usual value is total_examples=model.corpus_count.

In [220]:
#Infer a vector for new text => input a list of tokens
#model_dm.infer_vector(['the', 'patient', 'is', 'dead', '.'])


In [50]:
import gensim
# saves the doc2vec model to be used later.
#model_dm.save('./data/model_doc2vec_v2_600dim')

# open a saved doc2vec model 
model_dm=gensim.models.Doc2Vec.load('./data/model_doc2vec_v2_600dim')

#model_dm.wv.save_word2vec_format('./data/model_doc2vec_v2_600dim.txt', binary=False)


In [25]:
import re
def preprocessor_2(text):
    text = re.sub('<[^>]*>', '', text)
    text = re.sub('[\W]+', ' ', text.lower())
    #text = text.split()
    return text

test_set_clean=df_hadm_top10.iloc[idx_test]['text'].apply(preprocessor_2)

In [51]:
from time import time
t0 = time()
model_dm_600dim=test_set_clean.apply(model_dm.infer_vector)
elapsed=time() - t0
print("Time taken for Doc2vec pred over test set: ", elapsed, "seconds.")

('Time taken for Doc2vec pred over test set: ', 732.23779296875, 'seconds.')


In [52]:
import numpy as np

train_d2v=np.asarray(model_dm.docvecs)
df_train_d2v = pd.DataFrame(data=train_d2v, index=df_hadm_top10.iloc[idx_join_train]['id'])
test_d2v = [tuple(x) for x in model_dm_600dim]
df_test_d2v = pd.DataFrame(data=test_d2v, index=df_hadm_top10.iloc[idx_test]['id'])
df_d2v = pd.concat([df_train_d2v,df_test_d2v])


In [54]:
#save to drive            
df_d2v.to_csv("./data/model_doc2vec_v2_600dim_final.csv")


In [55]:
# Find the 10 most similar words
model_dm.most_similar('melanoma')

[('sarcoma', 0.3752405643463135),
 ('adenocarcinoma', 0.36460477113723755),
 ('cancer', 0.34577974677085876),
 ('carcinoma', 0.33788567781448364),
 ('melenoma', 0.3214113116264343),
 ('mole', 0.3124437928199768),
 ('leiomyosarcoma', 0.3108573257923126),
 ('tumor', 0.3053992688655853),
 ('nevus', 0.30361607670783997),
 ('lipoma', 0.29490727186203003)]

In [243]:
# Find 10 most similar docs
model_dm.docvecs.most_similar('note_0')

[('note_18392', 0.4303767681121826),
 ('note_22083', 0.4224788248538971),
 ('note_8182', 0.4058257043361664),
 ('note_28179', 0.394045352935791),
 ('note_7600', 0.3888844847679138),
 ('note_2749', 0.3831929564476013),
 ('note_34920', 0.3824225664138794),
 ('note_18099', 0.37785446643829346),
 ('note_20967', 0.3716892898082733),
 ('note_790', 0.37038496136665344)]